# Regresión  Radius Neighbors  (RN)

#### Datos de entrenamiento: 

$\quad D=\{\mathbf{X},\mathbf{y}\}, \quad \mathbf{X}\in \mathbb{R}^{N \times d}, \quad \mathbf{y} \in \mathbb{R}^N$ 

- Numero de datos de entrenamiento: $N$
- Número de atributos de los datos: $d$

Cada fila de $\mathbf{X}$ contiene un dato de entrenamiento, y la correspondiente fila de $\mathbf{y}$ es su etiqueta:

\begin{equation}
    \mathbf{X} =  
    \begin{bmatrix}
        \mathbf{x}_1 \\
        \mathbf{x}_2 \\
        \vdots \\
        \mathbf{x}_N
   \end{bmatrix}, 
   \quad \mathbf{y}=
    \begin{bmatrix}
    y_1 \\
    y_2 \\
    \vdots \\
    y_N
   \end{bmatrix} 
\end{equation}

#### Regresión RN: 
Sea $S_R(\mathbf{x})$ la hiperesfera de radio $R$ (de acuerdo a una métrica dada) centrada en el dato de test $\mathbf{x}$. Entonces la predicción para $\mathbf{x}$, 

\begin{equation}
\hat{y} (\mathbf{x}) = \frac{\sum_{n=1}^N \ I[\mathbf{x}_n \in S_R(\mathbf{x})] \ \ y_n} 
                            {\sum_{n=1}^N \ I[\mathbf{x}_n \in S_R(\mathbf{x})]  } 
\end{equation}

Es decir, la prediccion es el valor promedio de la variable objetivo de los datos de entrenamiento contenidos en $S_R(\mathbf{x})$.

#### Regresión RN ponderada: 
La predicción es la media ponderada de los valores de la variable objetivo de los datos de entrenamiento contenidos en $S_R(\mathbf{x})$. Los pesos de la ponderación son las distancias entre los datos de entrenamiento y el dato de test. 

\begin{equation}
\hat{y} (\mathbf{x}) = \frac{\sum_{n=1}^N \ I[\mathbf{x}_n \in S_R(\mathbf{x})] \ \ F(d(\mathbf{x},\mathbf{x}_n)) \ \ y_n} 
                            {\sum_{n=1}^N \ I[\mathbf{x}_n \in S_R(\mathbf{x})]  \ \ F(d(\mathbf{x},\mathbf{x}_n))} 
\end{equation}

donde $F(d)$ es una función decreciente de forma que se asigna más peso a los datos de entrenamiento que están más próximos al dato de test.

#### Distancias: 

- Minkowski: $\quad d(\mathbf{x}^{1}, \mathbf{x}^{2})= \left(\sum_{i=1}^d | \mathbf{x}_i^{1}-\mathbf{x}_i^{2}|^p \right)^{1/p}$
- Euclidea: $\quad d(\mathbf{x}^{1}, \mathbf{x}^{2})= \sqrt{\sum_{i=1}^d (\mathbf{x}_i^{1}-\mathbf{x}_i^{2})^2}$ 
- Chebyshev: $\quad d(\mathbf{x}^{1}, \mathbf{x}^{2})= \max_i | x_i^{1}-x_i^{2}|$
- Manhattan (o cityblock): $\quad d(\mathbf{x}^{1}, \mathbf{x}^{2})= \sum_{i=1}^d | x_i^{1}-x_i^{2}|$

La distancia euclidea es la de Minkowski cuando $p=2$. La distancia de Chebyshev es la de Minkowski cuando $p \rightarrow \inf$. La distancia Manhattan es la de Minkowski cuando $p=1$.

#### Hiperparámetros:

- Radio de las hiperesferas: $R$
- Exponente de la distancia de Minkowski: $d$
- Ponderación con distancias o no

#### Importa modulos

In [1]:
%matplotlib inline
import numpy as np

#### Carga base de datos
Importa la base de datos "diabetes" de scikit-learn

In [2]:
from sklearn import datasets
diabetes = datasets.load_diabetes()
X = diabetes.data   
y = diabetes.target

[N,d]=X.shape
print('No. de datos:',N)
print('No. de atributos originales:',d)

No. de datos: 442
No. de atributos originales: 10


#### Codificación One-Hot 
El segundo atributo es categórico, así que se codifica One-Hot.  

In [3]:
X1=np.copy(X)
X1[X[:,1]<0.0,1]=1
X1[X[:,1]>0.0,1]=2
X=X1
from sklearn.preprocessing import OneHotEncoder
codificacion = OneHotEncoder(categorical_features=[1])
codificacion.fit(X)  
X=codificacion.transform(X).toarray()
d=X.shape[1]
print('No. de atributos despues de codificar:',d)

No. de atributos despues de codificar: 11


#### Estandariza los datos

In [4]:
from sklearn import preprocessing 
estandariza=preprocessing.StandardScaler().fit(X)
X=estandariza.transform(X) 

#### Establece el modelo

In [5]:
from sklearn.neighbors import RadiusNeighborsRegressor
modelo = RadiusNeighborsRegressor() 

#### Hiperparámetros óptimos  

In [6]:
from sklearn.model_selection import GridSearchCV # parameters tunning
from sklearn.neighbors import RadiusNeighborsRegressor
print()
print('Regresion Radious Neighbor:')
parametros = { 'radius': np.arange(4.0, 4.5, 0.1),
               'p': np.arange(1.7, 2.0, 0.1),
               'weights': ['uniform','distance'] }

modelo = RadiusNeighborsRegressor() 
grid = GridSearchCV(modelo,parametros,cv=4,scoring='neg_mean_squared_error')
grid.fit(X,y)
radio=grid.best_params_['radius']
exponente=grid.best_params_['p']
pesos=grid.best_params_['weights']
print(' - Valores optimos de los hiperparametros:')
print('     radio:',radio,'    exponente:',exponente,'    pesos:',pesos)


# ---------------------------------------------------------------------
# Fija el modelo con los hiperparametros optimos
# ---------------------------------------------------------------------
modelo = RadiusNeighborsRegressor(radius=radio, p=exponente, weights=pesos) 
modelo.fit(X,y)

# ---------------------------------------------------------------------
# Cross Validation score sobre los datos de entrenamiento
# ---------------------------------------------------------------------
from sklearn.model_selection import cross_val_score
scores=cross_val_score(modelo,X,y,cv=4,scoring='neg_mean_squared_error')
print(" - Cross validation: Error RMS: %0.4f" % (np.sqrt(-scores.mean())))


Regresion Radious Neighbor:
 - Valores optimos de los hiperparametros:
     radio: 4.0     exponente: 1.7     pesos: distance
 - Cross validation: Error RMS: 58.8156
